Lambda School Data Science

*Unit 2, Sprint 1, Module 3*

---

# Ridge Regression

## Assignment

We're going back to our other **New York City** real estate dataset. Instead of predicting apartment rents, you'll predict property sales prices.

But not just for condos in Tribeca...

- [ ] Use a subset of the data where `BUILDING_CLASS_CATEGORY` == `'01 ONE FAMILY DWELLINGS'` and the sale price was more than 100 thousand and less than 2 million.
- [ ] Do train/test split. Use data from January — March 2019 to train. Use data from April 2019 to test.
- [ ] Do one-hot encoding of categorical features.
- [ ] Do feature selection with `SelectKBest`.
- [ ] Fit a ridge regression model with multiple features. Use the `normalize=True` parameter (or do [feature scaling](https://scikit-learn.org/stable/modules/preprocessing.html) beforehand — use the scaler's `fit_transform` method with the train set, and the scaler's `transform` method with the test set)
- [ ] Get mean absolute error for the test set.
- [ ] As always, commit your notebook to your fork of the GitHub repo.

The [NYC Department of Finance](https://www1.nyc.gov/site/finance/taxes/property-rolling-sales-data.page) has a glossary of property sales terms and NYC Building Class Code Descriptions. The data comes from the [NYC OpenData](https://data.cityofnewyork.us/browse?q=NYC%20calendar%20sales) portal.


## Stretch Goals

Don't worry, you aren't expected to do all these stretch goals! These are just ideas to consider and choose from.

- [ ] Add your own stretch goal(s) !
- [ ] Instead of `Ridge`, try `LinearRegression`. Depending on how many features you select, your errors will probably blow up! 💥
- [ ] Instead of `Ridge`, try [`RidgeCV`](https://scikit-learn.org/stable/modules/generated/sklearn.linear_model.RidgeCV.html).
- [ ] Learn more about feature selection:
    - ["Permutation importance"](https://www.kaggle.com/dansbecker/permutation-importance)
    - [scikit-learn's User Guide for Feature Selection](https://scikit-learn.org/stable/modules/feature_selection.html)
    - [mlxtend](http://rasbt.github.io/mlxtend/) library
    - scikit-learn-contrib libraries: [boruta_py](https://github.com/scikit-learn-contrib/boruta_py) & [stability-selection](https://github.com/scikit-learn-contrib/stability-selection)
    - [_Feature Engineering and Selection_](http://www.feat.engineering/) by Kuhn & Johnson.
- [ ] Try [statsmodels](https://www.statsmodels.org/stable/index.html) if you’re interested in more inferential statistical approach to linear regression and feature selection, looking at p values and 95% confidence intervals for the coefficients.
- [ ] Read [_An Introduction to Statistical Learning_](http://faculty.marshall.usc.edu/gareth-james/ISL/ISLR%20Seventh%20Printing.pdf), Chapters 1-3, for more math & theory, but in an accessible, readable way.
- [ ] Try [scikit-learn pipelines](https://scikit-learn.org/stable/modules/compose.html).

In [24]:
%%capture
import sys

# If you're on Colab:
if 'google.colab' in sys.modules:
    DATA_PATH = 'https://raw.githubusercontent.com/LambdaSchool/DS-Unit-2-Applied-Modeling/master/data/'
    !pip install category_encoders==2.*

# If you're working locally:
else:
    DATA_PATH = 'C:/Users/ryanh/DS-Unit-2-Linear-Models/data/'
    
# Ignore this Numpy warning when using Plotly Express:
# FutureWarning: Method .ptp is deprecated and will be removed in a future version. Use numpy.ptp instead.
import warnings
warnings.filterwarnings(action='ignore', category=FutureWarning, module='numpy')

In [25]:
# imports 
import pandas as pd
import pandas_profiling
import numpy as np

# Read New York City property sales data
df = pd.read_csv(DATA_PATH+'condos/NYC_Citywide_Rolling_Calendar_Sales.csv')

# Change column names: replace spaces with underscores
df.columns = [col.replace(' ', '_') for col in df]

# SALE_PRICE was read as strings.
# Remove symbols, convert to integer
df['SALE_PRICE'] = (
    df['SALE_PRICE']
    .str.replace('$','')
    .str.replace('-','')
    .str.replace(',','')
    .astype(int)
)

In [26]:
# BOROUGH is a numeric column, but arguably should be a categorical feature,
# so convert it from a number to a string
df['BOROUGH'] = df['BOROUGH'].astype(str)

In [27]:
# Reduce cardinality for NEIGHBORHOOD feature

# Get a list of the top 10 neighborhoods
top10 = df['NEIGHBORHOOD'].value_counts()[:10].index

# At locations where the neighborhood is NOT in the top 10, 
# replace the neighborhood with 'OTHER'
df.loc[~df['NEIGHBORHOOD'].isin(top10), 'NEIGHBORHOOD'] = 'OTHER'

In [28]:
# look at profile report for df  

df.profile_report()

In [ ]:
# Use a subset of the data where BUILDING_CLASS_CATEGORY == '01 ONE FAMILY DWELLINGS' 
# and the sale price was more than 100,000 and less than 2,000,000

df = df[df['BUILDING_CLASS_CATEGORY'] == '01 ONE FAMILY DWELLINGS']
df = df[(100000 < df['SALE_PRICE']) & (df['SALE_PRICE'] < 2000000)]

In [ ]:
# fill missing values with mean and inspect head

df = df.fillna(value=df.mean(skipna=True))
df.head()

In [ ]:
# inspect data type of each column

df.dtypes

In [ ]:
# Do train/test split. Train data from January — March 2019. Test data from April 2019.

df['SALE_DATE'] = pd.to_datetime(df['SALE_DATE'])
train = df[(np.datetime64('2019-01-01') <= df['SALE_DATE']) & (df['SALE_DATE'] < np.datetime64('2019-04-01'))]
test = df[(np.datetime64('2019-04-01') <= df['SALE_DATE'] ) & (df['SALE_DATE'] < np.datetime64('2019-05-01'))]

In [ ]:
# one-hot encoding on categorical features 

target = 'SALE_PRICE'
high_cardinality = ['ADDRESS', 'APARTMENT_NUMBER', 'SALE_DATE', 'EASE-MENT']

X_train = train.drop(axis=1, labels=[target] + high_cardinality)
X_test = test.drop(axis=1, labels=[target] + high_cardinality)

y_train = train[target]
y_test = test[target]

import category_encoders as ce

encoder = ce.OneHotEncoder(use_cat_names=True)
X_train = encoder.fit_transform(X_train)
X_test = encoder.transform(X_test)

In [34]:
# look at X_train head

X_train.head()

BOROUGH_3  BOROUGH_4  BOROUGH_2  BOROUGH_5  BOROUGH_1  \
44           1          0          0          0          0   
61           0          1          0          0          0   
78           0          0          1          0          0   
108          1          0          0          0          0   
111          1          0          0          0          0   

     NEIGHBORHOOD_OTHER  NEIGHBORHOOD_FLUSHING-NORTH  \
44                    1                            0   
61                    1                            0   
78                    1                            0   
108                   1                            0   
111                   1                            0   

     NEIGHBORHOOD_BEDFORD STUYVESANT  NEIGHBORHOOD_FOREST HILLS  \
44                                 0                          0   
61                                 0                          0   
78                                 0                          0   
108                                0                          0   
111                                0                          0   

     NEIGHBORHOOD_BOROUGH PARK  ...  BUILDING_CLASS_AT_TIME_OF_SALE_A1  \
44                           0  ...                                  0   
61                           0  ...                                  1   
78                           0  ...                                  1   
108                          0  ...                                  1   
111                          0  ...                                  0   

     BUILDING_CLASS_AT_TIME_OF_SALE_A5  BUILDING_CLASS_AT_TIME_OF_SALE_A0  \
44                                   0                                  0   
61                                   0                                  0   
78                                   0                                  0   
108                                  0                                  0   
111                                  1                                  0   

     BUILDING_CLASS_AT_TIME_OF_SALE_A2  BUILDING_CLASS_AT_TIME_OF_SALE_A3  \
44                                   0                                  0   
61                                   0                                  0   
78                                   0                                  0   
108                                  0                                  0   
111                                  0                                  0   

     BUILDING_CLASS_AT_TIME_OF_SALE_S1  BUILDING_CLASS_AT_TIME_OF_SALE_A4  \
44                                   0                                  0   
61                                   0                                  0   
78                                   0                                  0   
108                                  0                                  0   
111                                  0                                  0   

     BUILDING_CLASS_AT_TIME_OF_SALE_A6  BUILDING_CLASS_AT_TIME_OF_SALE_A8  \
44                                   0                                  0   
61                                   0                                  0   
78                                   0                                  0   
108                                  0                                  0   
111                                  0                                  0   

     BUILDING_CLASS_AT_TIME_OF_SALE_S0  
44                                   0  
61                                   0  
78                                   0  
108                                  0  
111                                  0  

[5 rows x 934 columns]

In [35]:
# look at X_test head

X_test.head()

BOROUGH_3  BOROUGH_4  BOROUGH_2  BOROUGH_5  BOROUGH_1  \
18235          0          0          1          0          0   
18239          0          0          1          0          0   
18244          1          0          0          0          0   
18280          1          0          0          0          0   
18285          1          0          0          0          0   

       NEIGHBORHOOD_OTHER  NEIGHBORHOOD_FLUSHING-NORTH  \
18235                   1                            0   
18239                   1                            0   
18244                   1                            0   
18280                   1                            0   
18285                   1                            0   

       NEIGHBORHOOD_BEDFORD STUYVESANT  NEIGHBORHOOD_FOREST HILLS  \
18235                                0                          0   
18239                                0                          0   
18244                                0                          0   
18280                                0                          0   
18285                                0                          0   

       NEIGHBORHOOD_BOROUGH PARK  ...  BUILDING_CLASS_AT_TIME_OF_SALE_A1  \
18235                          0  ...                                  1   
18239                          0  ...                                  0   
18244                          0  ...                                  1   
18280                          0  ...                                  0   
18285                          0  ...                                  0   

       BUILDING_CLASS_AT_TIME_OF_SALE_A5  BUILDING_CLASS_AT_TIME_OF_SALE_A0  \
18235                                  0                                  0   
18239                                  0                                  0   
18244                                  0                                  0   
18280                                  1                                  0   
18285                                  0                                  0   

       BUILDING_CLASS_AT_TIME_OF_SALE_A2  BUILDING_CLASS_AT_TIME_OF_SALE_A3  \
18235                                  0                                  0   
18239                                  1                                  0   
18244                                  0                                  0   
18280                                  0                                  0   
18285                                  0                                  0   

       BUILDING_CLASS_AT_TIME_OF_SALE_S1  BUILDING_CLASS_AT_TIME_OF_SALE_A4  \
18235                                  0                                  0   
18239                                  0                                  0   
18244                                  0                                  0   
18280                                  0                                  0   
18285                                  0                                  0   

       BUILDING_CLASS_AT_TIME_OF_SALE_A6  BUILDING_CLASS_AT_TIME_OF_SALE_A8  \
18235                                  0                                  0   
18239                                  0                                  0   
18244                                  0                                  0   
18280                                  0                                  0   
18285                                  0                                  0   

       BUILDING_CLASS_AT_TIME_OF_SALE_S0  
18235                                  0  
18239                                  0  
18244                                  0  
18280                                  0  
18285                                  0  

[5 rows x 934 columns]

In [ ]:
# feature selection with SelectKBest.

from sklearn.feature_selection import SelectKBest, f_regression
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error

def getMAE(X_train, y_train, X_test, y_test, k=10):
    selector = SelectKBest(score_func=f_regression, k=k)
    X_train_selected = selector.fit_transform(X_train, y_train)
    X_test_selected = selector.transform(X_test)

    model = LinearRegression()
    model.fit(X_train_selected, y_train)
    y_pred = model.predict(X_test_selected)

    mae = mean_absolute_error(y_pred, y_test)
    return mae

maes = [getMAE(X_train, y_train, X_test, y_test, k=k) for k in range(1, len(X_train.columns)+1)]

In [ ]:
# create a scree plot

from plotly import graph_objects as go

fig = go.Figure()

fig.add_trace(
    go.Bar(
        x=list(range(1, len(maes)+1)),
        y=maes,
    )
)

fig.update_yaxes(range=(100000, 200000))

fig.show()

In [ ]:
selector = SelectKBest(score_func=f_regression, k=21)
X_train_selected = selector.fit_transform(X_train, y_train)
X_test_selected = selector.transform(X_test)

model = RidgeCV(alphas=[10**x for x in range(-5, 6)], normalize=True)
model.fit(X_train, y_train)
y_pred = model.predict(X_test)

mae = mean_absolute_error(y_pred, y_test)

print(f"""
MAE: {mae}
alpha: {model.alpha_}
""")

In [ ]:
alphas = [10.**(x/100.) for x in range(-600, -25)]
print("alphas")
print(alphas)

model = RidgeCV(alphas=alphas, normalize=True)
model.fit(X_train_selected, y_train)
y_pred = model.predict(X_test_selected)

mae = mean_absolute_error(y_pred, y_test)

print(f"""
MAE: {mae}
alpha: {model.alpha_}
""")